## Project Goals
- Scrape Amazon product prices, ratings, and reviews
- Build a Power BI / Tableau dashboard for visualization and analysis

## Scraping Amazon

### Install libraries


In [1]:
!pip3 install fake-useragent==1.5.1
!pip3 install --upgrade pip setuptools wheel
!pip3 install requests beautifulsoup4 pandas numpy


Defaulting to user installation because normal site-packages is not writeable
Defaulting to user installation because normal site-packages is not writeable
Defaulting to user installation because normal site-packages is not writeable


### Scrape Amazon Product Data

In [1]:
import requests
from bs4 import BeautifulSoup
import pandas as pd
import concurrent.futures
import random
import time
import threading
from fake_useragent import UserAgent

# Custom headers to mimic a real browser
user_agent = UserAgent()
headers = {"User-Agent": user_agent.random}  # random user agent
custom_headers = {
    'User-Agent': "Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/120.0.0.0 Safari/537.36",
    'Accept-Language': 'da, en-gb, en',
    'Accept-Encoding': 'gzip, deflate, br',
    'Accept': 'text/html,application/xhtml+xml,application/xml;q=0.9,image/avif,image/webp,*/*;q=0.8',
    'Referer': 'https://www.google.com/'
}

# Search queries and number of pages to scrape
num_pages = 7
search_queries =["skincare", "serum", "sun+screen", "moisturizer", "cleanser", "toner", "retinol+cream", "sheet+mask", "face+oil", "cleansing+oil", "night+cream", "korean+skincare"] #"gel+moisturizer"
product_list = []
lock = threading.Lock()  # To ensure thread-safe data collection

# Function to fetch HTML content with retries
def fetch(url):
    print(f"🟡 Fetching URL: {url}")

    for _ in range(3):  # Retry up to 3 times
        try:
            time.sleep(random.uniform(5,15))  # Add delay to avoid detection
            response = requests.get(url, headers=custom_headers, timeout=10)

            print(f"🟢 Response Status Code: {response.status_code}")
            
            if response.status_code == 200:
                print("✅ Successfully fetched HTML")
                return response.text  # Returns HTML

            elif response.status_code == 503:
                print(f"❌ CAPTCHA Detected for {url} (503)")
                return None 
            
            else:
                print(f"❌ Other Error: {response.status_code} on {url}")
                return None  # Other errors

        except requests.RequestException as e:
            print(f"❌ Request failed: {e}")
            time.sleep(random.uniform(2, 4))  # Retry delay

    return None

# Function to scrape product listings from search page
def scrape_search_page(search_query, page):
    url = f"https://www.amazon.com/s?k={search_query}&page={page}"
    html = fetch(url) #calls fetch function

    if html:
        soup = BeautifulSoup(html, "html.parser")
        products = soup.find_all("div", {"data-component-type": "s-search-result"})

        if not products:
            print(f"❌ No products found on page {page} for {search_query}. Check the HTML structure.")
            return
        
        for product in products:
            title_tag = product.find("h2", class_="a-size-base-plus")
            link_tag = product.find("a", class_="a-link-normal s-no-outline")
            price_tag = product.find("span", {"class": "a-price"})
            original_price_div = product.find("div", class_="a-section aok-inline-block")
            original_price_tag = original_price_div.find("span", class_="a-offscreen") if original_price_div else None
            brand_tag = product.find("span", class_="a-size-base-plus a-color-base")  # Brand in search page
            num_ratings_tag = product.find("span", {"class": "a-size-base s-underline-text"})
            rating_tag = product.find("span", class_="a-icon-alt")

            if title_tag and link_tag:
                title = title_tag.text.strip()
                product_url = f"https://www.amazon.com{link_tag['href']}"

                # Extract prices/ratings/brand
                price = price_tag.find("span", class_="a-offscreen").text.strip() if price_tag and price_tag.find("span", class_="a-offscreen") else "N/A"
                original_price = original_price_tag.text.strip() if original_price_tag else "N/A"
                num_ratings = num_ratings_tag.text.strip() if num_ratings_tag else "N/A"
                rating = rating_tag.text.strip() if rating_tag else "N/A"
                brand = brand_tag.text.strip() if brand_tag else "N/A"

                print(f"✅ Extracted: Title={title}, Brand={brand}, Price={price}, URL={product_url}")

                # Append product to list
                with lock:
                    product_list.append([title, brand, price, original_price, rating, num_ratings, product_url])
                    print(f"📌 Appended to product_list: {title} | Brand: {brand}")

                # If brand is missing, scrape product page
                if brand == "N/A":
                    print(f"🔍 No brand found. Scraping PDP for {title}...")
                    scrape_product_page(title, product_url, price, original_price, rating, num_ratings)

        print(f"✅ Scraped {len(products)} products from search results for query: {search_query}, page {page}")

    else:
        print(f"❌ Failed to fetch HTML for {url}. Check internet connection or CAPTCHA!")

# Function to scrape product details from a product pag
def scrape_product_page(title, product_url, search_price, search_original_price, rating, num_ratings):
    html = fetch(product_url)

    if html:
        soup = BeautifulSoup(html, "html.parser")

        # Extract brand from PDP
        brand = "N/A"
        brand_tag = soup.find("a", {"id": "bylineInfo"})
        if brand_tag:
            brand = brand_tag.text.strip()

        print(f"Scraping Product Page: {title}, Brand: {brand}, Price: {search_price}")

        # Append data to the product list
        with lock:
            product_list.append([title, brand, search_price, search_original_price, rating, num_ratings, product_url])

# Main function to execute multi-threaded scraping
def main():
    with concurrent.futures.ThreadPoolExecutor(max_workers=5) as executor:
        task_list = []
        for search_query in search_queries:
            for page in range(1, num_pages + 1):
                task_list.append(executor.submit(scrape_search_page, search_query, page))

        # Wait for all tasks to complete
        concurrent.futures.wait(task_list)

# Run scraper
start_time = time.time()
main()
end_time = time.time()

# Save results to an Excel file
df = pd.DataFrame(product_list, columns=["title", "brand", "price", "original price", "rating", "number of ratings", "product url"])
df.to_excel("amazon_multithreaded_new.xlsx", index=False)
print(f"✅ Scraping complete in {end_time - start_time:.2f} seconds & saved to 'amazon_multithreaded_new.xlsx'")


/Users/michiko/Library/Python/3.9/lib/python/site-packages/urllib3/__init__.py:35: NotOpenSSLWarning: urllib3 v2 only supports OpenSSL 1.1.1+, currently the 'ssl' module is compiled with 'LibreSSL 2.8.3'. See: https://github.com/urllib3/urllib3/issues/3020
  warnings.warn(


🟡 Fetching URL: https://www.amazon.com/s?k=skincare&page=1🟡 Fetching URL: https://www.amazon.com/s?k=skincare&page=2

🟡 Fetching URL: https://www.amazon.com/s?k=skincare&page=3
🟡 Fetching URL: https://www.amazon.com/s?k=skincare&page=4
🟡 Fetching URL: https://www.amazon.com/s?k=skincare&page=5
🟢 Response Status Code: 200
✅ Successfully fetched HTML
✅ Extracted: Title=Paula's Choice SKIN PERFECTING 2% BHA Liquid Salicylic Acid Exfoliant-Facial Exfoliant for Blackheads, Enlarged Pores, Wrinkles & Fine Lines, Brand=N/A, Price=$41.65, URL=https://www.amazon.com/sspa/click?ie=UTF8&spc=MTo3ODMyNDE3MjM4MzU5MDMzOjE3MzkyNDEzOTc6c3BfYXRmX25leHQ6MzAwNjU1NzUwMTczMDAyOjowOjo&url=%2FPaulas-Choice-SKIN-PERFECTING-Salicylic-Exfoliant%2Fdp%2FB07D8DBS7S%2Fref%3Dsr_1_193_sspa%3Fdib%3DeyJ2IjoiMSJ9.BahEDZZdEHG8lpH9eZvcOFJEMKNpfExeF58G-PQwcaSAjbildnsvD3kYESu5ebcKngiKO9hsf1ESHoFuSQDvNlPhrXXQTRQb4QIBIeF-1bxSqS9ly95TgiqtYguTl5RkLVG11Kz4wtYfvRFwQiqhiboKYXmGgkz2UbYRCFogM8wV5MyVrIS_XKLwWO9kp9YXqhg6OUffwlO_HwCVqQF

### Clean and prepare data
- Check and fix for missing values
- Remove duplicates


In [6]:
import pandas as pd
import re

#Function to extract brand
def extract_brand(text):
    if pd.notna(text): 
        if "Visit the" in text:
            match = re.search(r"Visit the (.+?) Store", text)
        elif "Brand:":
            match = re.search(r"Brand: \s*(.+)",text)
        else:
            return text
        
        if match:
            return match.group(1)
        
    return text


df = pd.read_excel("amazon_multithreaded_new.xlsx")

#Remove rows with missing titles/prices
df.dropna(subset=["title", "brand" ,"price", "number of ratings"], inplace=True)

# Remove duplicates
df.drop_duplicates(subset=["title"], keep="first", inplace=True)

# Convert N/A to pandas NA
df.replace("N/A", pd.NA, inplace=True)

# Fill missing values
df.fillna({"brand": "Unknown", "rating": "No rating", "number of ratings": 0}, inplace=True)

#Extract the brand name
df["brand"] = df["brand"].apply(extract_brand)

#Extract the numeric part only in the rating
df["rating"] = df["rating"].str.extract(r"([\d.]+)").astype(float)

#Remove $ and conver to float
df["price"] = df["price"].astype(str).str.replace(",", "").str.replace("$", "").astype(float)
df["original price"] = df["original price"].astype(str).str.replace(",", "").str.replace("$", "").astype(float)

#Remove commas
df["number of ratings"] = df["number of ratings"].astype(str).str.replace(",", "").astype(int)

df.to_excel("clean_amazon_data.xlsx", index=False)

df.sample(20)


title             brand  \
319   Bubble Skincare Cloud Surf Water Cream Face Mo...   Bubble Skincare   
787   Pure Natural Skin Brightening & Anti Aging 20%...            Srripo   
5399  Lululun 32pc Sheet Facial Mask, Patented Daily...           Lululun   
7210  Andalou Natural Purple Carrot + C Luminous Nig...  Andalou Naturals   
1151  COSRX Niacinamide 5% + Snail Mucin 74% Dual Es...             COSRX   
3872  No.1 Toner | Pure-Full Calming Herb Toner | Br...          numbuzin   
7544  Versed Sweet Relief Night Mask + Face Balm - I...            Versed   
1053  MAELOVE Vitamin C Serum, Glow Maker with Vitam...           MAELOVE   
6704  Sunflower & Moringa Fresh Cleanse Oil for Face...       AbsoluteJOI   
167   Medicube Zero Exosome Shot 2,000 PPM Spicule F...          medicube   
2049  Badger Reef Safe Sunscreen, SPF 40 Sport Miner...            Badger   
1647  Coppertone SPORT Sunscreen SPF 30 Lotion, Wate...        Coppertone   
2521  No7 Restore & Renew Multi Action Face & Neck S...               No7   
1395  Anua PDRN Hyaluronic Acid Capsule 100 Serum, R...              ANUA   
5870  CENTELLIAN 24 Madeca Mask (Mela, 20pc, 16.9fl ...     CENTELLIAN 24   
6926  Micellar Water with Rose Water and Glycerin, H...           Garnier   
2041  COOLA Organic Face Sunscreen SPF 50 Sunblock L...             COOLA   
4180  Madagascar Centella Probio-CICA Essence Toner ...          SKIN1004   
3665  Rice 70 Glow Milky Toner, for Glass Skin, Rice...              ANUA   
3909  414X High Yield Toner Cartridges 4 Pack (with ...       S SMARTOMNI   

       price  original price  rating  number of ratings  \
319    14.98           17.00     4.7                332   
787    49.99             NaN     4.8                167   
5399   26.99             NaN     4.4               1264   
7210   13.42           26.99     4.5               1382   
1151   24.50           28.00     4.5               5551   
3872   16.80             NaN     4.3                511   
7544   11.33           17.99     4.1                220   
1053   39.48             NaN     4.4                350   
6704   45.00             NaN     4.6                  9   
167    17.90           39.00     4.4               1337   
2049   15.29             NaN     4.5               3588   
1647    7.98             NaN     4.7               2443   
2521   15.10           24.99     4.6               2968   
1395   28.00             NaN     4.4                 35   
5870   24.98             NaN     4.3                 56   
6926    8.97           11.99     4.7              23086   
2041   32.00             NaN     4.6               2309   
4180   14.74           15.49     4.6                242   
3665   22.00             NaN     4.5                662   
3909  139.99          159.99     4.1               1105   

                                            product url  
319   https://www.amazon.com/Bubble-Skincare-Cloud-W...  
787   https://www.amazon.com/Brightening-Collagen-Hy...  
5399  https://www.amazon.com/Lululun-Hydrating-Moist...  
7210  https://www.amazon.com/Andalou-Naturals-Purple...  
1151  https://www.amazon.com/COSRX-Advanced-Snail-Ra...  
3872  https://www.amazon.com/numbuzin-Pure-Full-Acne...  
7544  https://www.amazon.com/Versed-Sweet-Relief-Nig...  
1053  https://www.amazon.com/Maelove-Glow-Maker-Vita...  
6704  https://www.amazon.com/sspa/click?ie=UTF8&spc=...  
167   https://www.amazon.com/Medicube-Exosome-Spicul...  
2049  https://www.amazon.com/Badger-Sunscreen-Unscen...  
1647  https://www.amazon.com/Coppertone-Sunscreen-Lo...  
2521  https://www.amazon.com/No7-Restore-Renew-Cream...  
1395  https://www.amazon.com/Hyaluronic-Hydration-Mo...  
5870  https://www.amazon.com/CENTELLIAN-24-Madeca-Ma...  
6926  https://www.amazon.com/Garnier-SkinActive-Mice...  
2041  https://www.amazon.com/Sunscreen-Spectrum-Ligh...  
4180  https://www.amazon.com/SKIN1004-Madagascar-Cen...  
3665  https://www.amazon.com/ANUA-Brightening-Niacin...  
3909  https://www.amazon.com/ssp